In [1]:
import os
import sys
sys.path.append("../")
import yaml
import json
import argparse
import numpy as np
from PIL import Image
import torch

from minigpt4.common.registry import registry
from minigpt4.models import load_from_cfg
from minigpt4.conversation.conversation import Chat_7132k as Chat
import copy
import re

from transformers import AutoModelForCausalLM, AutoTokenizer
from transformers.generation import GenerationConfig
from PIL import Image,ImageDraw,ImageFont
from matplotlib import pyplot as plt

import openai
import json

import os
from tqdm import tqdm
import pandas as pd
import numpy as np
from collections import Counter
import time 

from transformers import AutoModel, AutoTokenizer
#new_path = '/mnt/petrelfs/share_data/dongxiaoyi/share_models/amp002_4000'
#new_path = '/mnt/petrelfs/share_data/dongxiaoyi/share_models/Int2_PLoRA_ViG/'
new_path = '/mnt/hwfile/mllm/xiaoyidong/share_model/FHD2_R560_IHD24x1_S3_0618/step_2300/'
tokenizer = AutoTokenizer.from_pretrained(new_path, trust_remote_code=True)
#model = AutoModel.from_pretrained(new_path, device_map='cuda', torch_dtype=torch.float16, trust_remote_code=True)
model = AutoModelForCausalLM.from_pretrained(new_path, device_map="cuda", trust_remote_code=True).eval().cuda().to(torch.bfloat16)
#model = AutoModel.from_pretrained(new_path, torch_dtype=torch.bfloat16, trust_remote_code=True).cuda().eval()
model.cuda()
model.tokenizer = tokenizer


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /mnt/petrelfs/dongxiaoyi/anaconda3/envs/intern2/lib/python3.9/site-packages/bitsandbytes/libbitsandbytes_cuda117.so
CUDA SETUP: CUDA runtime path found: /mnt/petrelfs/share_data_old/llm_env/dep/cuda-11.7/lib64/libcudart.so.11.0
CUDA SETUP: Highest compute capability among GPUs detected: 8.0
CUDA SETUP: Detected CUDA version 117
CUDA SETUP: Loading binary /mnt/petrelfs/dongxiaoyi/anaconda3/envs/intern2/lib/python3.9/site-packages/bitsandbytes/libbitsandbytes_cuda117.so...


/mnt/petrelfs/dongxiaoyi/anaconda3/envs/intern2/lib/python3.9/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: /mnt/petrelfs/dongxiaoyi/anaconda3/envs/intern2 did not contain ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] as expected! Searching further paths...
  warn(msg)
/mnt/petrelfs/dongxiaoyi/anaconda3/envs/intern2/lib/python3.9/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/mnt/petrelfs/dongxiaoyi/anaconda3/envs/intern2/lib/python3.9/site-packages/cv2/../../lib64')}
  warn(msg)


Set max length to 4480


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [21]:
import re
import os
import json
import base64
import torch
import openai
import numpy as np
import torchvision
from PIL import Image
from typing import Optional
from torch.utils.data import Dataset
import torchvision.transforms as transforms
from torchvision.transforms.functional import InterpolationMode

def padding_336(b, pad=336):
    width, height = b.size
    tar = int(np.ceil(height / pad) * pad)
    top_padding = 0 # int((tar - height)/2)
    bottom_padding = tar - height - top_padding
    left_padding = 0
    right_padding = 0
    b = transforms.functional.pad(b, [left_padding, top_padding, right_padding, bottom_padding], fill=[255,255,255])

    return b

def HD_transform(img, hd_num=25):
    width, height = img.size
    trans = False
    if width < height:
        img = img.transpose(Image.TRANSPOSE)
        trans = True
        width, height = img.size
    ratio = (width/ height)
    scale = 1
    while scale*np.ceil(scale/ratio) <= hd_num:
        scale += 1
    scale -= 1
    scale = min(np.ceil(width / 560), scale)
    new_w = int(scale * 560)
    new_h = int(new_w / ratio)
    print (scale, f'{height}/{new_h}, {width}/{new_w}')

    img = transforms.functional.resize(img, [new_h, new_w],)
    img = padding_336(img, 560)
    width, height = img.size
    if trans:
        img = img.transpose(Image.TRANSPOSE)

    return img

def Identity_transform(img, hd_num=25):
    width, height = img.size
    trans = False
    if width < height:
        img = img.transpose(Image.TRANSPOSE)
        trans = True
        width, height = img.size
    ratio = (width/ height)
    scale = 1
    new_h = int(scale * 560)
    new_w = int(new_h * ratio)
    print (new_h, new_w)

    img = transforms.functional.resize(img, [new_h, new_w],)
    img = img.transpose(Image.TRANSPOSE)
    img = padding_336(img, 560)
    width, height = img.size
    if not trans:
        img = img.transpose(Image.TRANSPOSE)

    return img

def model_gen(model, text, images, need_bos=True, hd_num=36, max_new_token = 256, beam=3, do_sample=False):
    pt1 = 0
    embeds = []
    im_mask = []
    if images is None:
        images = []
        images_loc = []
    else:
        images = [images]
        images_loc = [0]
    for i, pts in enumerate(images_loc + [len(text)]):
        subtext = text[pt1:pts]
        if need_bos or len(subtext) > 0:
            text_embeds = model.encode_text(subtext, add_special_tokens=need_bos)
            embeds.append(text_embeds)
            im_mask.append(torch.zeros(text_embeds.shape[:2]).cuda())
            need_bos = False
        if i < len(images):
            try:
                image = Image.open(images[i]).convert('RGB')
            except:
                image = images[i].convert('RGB')

            
            image = HD_transform(image, hd_num=hd_num)
            image = model.vis_processor(image).unsqueeze(0).cuda()
            image_embeds = model.encode_img(image)
            print (image_embeds.shape)
            embeds.append(image_embeds)
            im_mask.append(torch.ones(image_embeds.shape[:2]).cuda())
        pt1 = pts
    embeds = torch.cat(embeds, dim=1)
    im_mask = torch.cat(im_mask, dim=1)
    im_mask = im_mask.bool()
    #print (im_mask)
    
    #embeds = embeds.repeat(2,1,1)
    #im_mask = im_mask.repeat(2,1,1)
    outputs = model.generate(inputs_embeds=embeds, im_mask=im_mask,
                        temperature=1.0, max_new_tokens=max_new_token, num_beams=beam,
                        do_sample=False, repetition_penalty=1.00)

    output_token = outputs[0]
    if output_token[0] == 0 or output_token[0] == 1:
        output_token = output_token[1:]
    output_text = model.tokenizer.decode(output_token, add_special_tokens=False)
    output_text = output_text.split('[UNUSED_TOKEN_145]')[0].strip()
    return output_text

In [7]:
import os
from tqdm import tqdm
from io import BytesIO
from PIL import Image
import json
import copy
import pandas as pd
import random
from PIL import Image, ImageDraw, ImageFont
from petrel_client.client import Client
client = Client("~/petreloss.conf")

In [8]:
import os
import sys 
import yaml
import json
import argparse
import numpy as np
from PIL import Image
import torch

from minigpt4.common.registry import registry
from minigpt4.models import load_from_cfg
from minigpt4.conversation.conversation import Chat_7132k as Chat
import copy
import re

from transformers import AutoModelForCausalLM, AutoTokenizer
from transformers.generation import GenerationConfig
from PIL import Image,ImageDraw,ImageFont
from matplotlib import pyplot as plt

import openai
import json

import os
from tqdm import tqdm
import pandas as pd
import numpy as np
from collections import Counter
import time 

from transformers import AutoModel, AutoTokenizer
import re
import os
import json
import base64
import torch
import openai
import numpy as np
import torchvision
from PIL import Image
from typing import Optional
from torch.utils.data import Dataset
import torchvision.transforms as transforms
from torchvision.transforms.functional import InterpolationMode
import torch
import numpy as np
from PIL import Image
import matplotlib.pyplot as plt
from decord import VideoReader
def load_video(vis_path, num_frm=32, start=None, end=None):
        vid = VideoReader(vis_path, num_threads=1)
        fps = vid.get_avg_fps()
        t_stride = int(2 * round(float(fps) / int(1)))
        start_idx = 0 if start is None else start
        end_idx = len(vid) if end is None else end
        all_pos = list(range(start_idx, end_idx, t_stride))
        images = [vid[i].numpy() for i in all_pos]
        if len(images) > num_frm:
            num_frm = min(num_frm, len(images))
            step_size = len(images) / (num_frm + 1)
            indices = [int(i*step_size) for i in range(num_frm)]
            images = [images[i] for i in indices]
        images = [Image.fromarray(arr) for arr in images]
        print (len(images))
        return images


In [9]:
def img_process(imgs):
    new_imgs = []
    for img in imgs:
        w, h = img.size
        scale = w/h
        if w > h:
            new_w = 560 * 2
            new_h = int(560 * 2 / scale)
        else:
            new_w = int(560 * 2 * scale)
            new_h = 560 * 2
        img = transforms.functional.resize(img, [new_h, new_w],)
        new_imgs.append(img)
    imgs = new_imgs
    new_w = 0
    new_h = 0
    pad = 40
    if w > h:
        for im in imgs:
            w,h = im.size
            new_w = max(new_w, w)
            new_h += h + 10 + pad
        font = ImageFont.truetype("/mnt/petrelfs/dongxiaoyi/SimHei.ttf", pad)
        new_img = Image.new('RGB', (new_w, new_h), 'white')
        draw = ImageDraw.Draw(new_img)
        curr_h = 0
        for idx, im in enumerate(imgs):
            w,h = im.size
            new_img.paste(im, (0, pad + curr_h))
            draw.text((0, curr_h ), f'<IMAGE {idx}>', font=font, fill='black')
            if idx + 1 < len(imgs):
                draw.line([(0, pad +curr_h + h +5), (new_w, pad +curr_h + h +5)], fill = 'black', width=2)
            curr_h += h + 10 + pad
        #print (new_w, new_h)
    else:
        for im in imgs:
            w,h = im.size
            new_w += w + 10
            new_h = max(new_h, h)
        new_h += pad
        font = ImageFont.truetype("/mnt/petrelfs/dongxiaoyi/SimHei.ttf", pad)
        new_img = Image.new('RGB', (new_w, new_h), 'white')
        draw = ImageDraw.Draw(new_img)
        curr_w = 0
        for idx, im in enumerate(imgs):
            w,h = im.size
            new_img.paste(im, (curr_w, pad))
            draw.text((curr_w, 0), f'<IMAGE {idx}>', font=font, fill='black')
            if idx + 1 < len(imgs):
                draw.line([(curr_w + w + 5, 0), (curr_w + w + 5, new_h)], fill = 'black', width=2)
            curr_w += w + 10
    return new_img

In [7]:
import pandas as pd
f = pd.read_excel('/mnt/hwfile/opencompass/dhd/main_table_result/Proprietary_LVLM/GPT-4o/frame_16/GPT4o_HIGH_frame16_pack1_seed-1/gpt-4-1106_rating.xlsx')

In [8]:
a = [i for i in range(len(f))]
#rank = int(sys.argv[1])
rank = 0
world_size = 8

part_len = len(a) // world_size

if rank == world_size - 1:
    a = a[part_len*rank: ]
else:
    a = a[part_len*rank: part_len*(rank+1)]

In [9]:
out = []
for i in tqdm(a[:]):
    v = f['video'][i]
    video = f'/mnt/hwfile/opencompass/dhd/MMBench-Video/video/{v}.mp4'
    imgs = load_video(video,num_frm=32) 
    img = img_process(imgs)
    #plt.imshow(img)
    #plt.show()
    q =  '' + f['question'][i] 
    query = f'[UNUSED_TOKEN_146]user\n{q} Answer this question in detail.\n[UNUSED_TOKEN_145]\n[UNUSED_TOKEN_146]assistant\n'
    with torch.cuda.amp.autocast(): 
        response = model_gen(model, query, img, hd_num=32, do_sample=False, max_new_token = 512, beam=3)
    print (query, '####\n',response, '####\n',f['answer'][i]) 
    print ('##################')
    temp = {
        'index': i,
        'question': f['question'][i],
        'answer': f['answer'][i],
        'prediction': response
    } 
    out.append(temp)

  0%|                                                                                                                                                                                                                | 0/249 [00:00<?, ?it/s]

32
560 10880
torch.Size([1, 8821, 4096])


  0%|▊                                                                                                                                                                                                     | 1/249 [00:24<1:41:10, 24.48s/it]

[UNUSED_TOKEN_146]user
What is the name of the player who scored the first goal in the video? Answer this question in detail.
[UNUSED_TOKEN_145]
[UNUSED_TOKEN_146]assistant
 ####
 I'm unable to provide the name of the player who scored the first goal in the video. The video content does not reveal the player's identity, and as an AI, I don't have the capability to recognize or remember specific individuals based on their appearance in images or videos. My responses are limited to the information provided within the content of the question itself, and in this case, the video content does not include the name of the player. ####
 Palmer.
##################
32
560 10880
torch.Size([1, 8821, 4096])


  1%|█▌                                                                                                                                                                                                    | 2/249 [00:56<1:59:19, 28.99s/it]

...

[UNUSED_TOKEN_146]user
What has the police car in the video been looking for? Answer this question in detail.
[UNUSED_TOKEN_145]
[UNUSED_TOKEN_146]assistant
 ####
 In the video, the police car has been looking for a siren. It starts by asking various characters if they have seen it, including a bear and a dog. The police car then proceeds to search through a box of presents, hoping to find the siren among them. After checking the box, the police car continues its search on the street, eventually finding the siren attached to the back of a bus. ####
 It's looking for a siren.
##################
32
560 10880
torch.Size([1, 8821, 4096])


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▏| 248/249 [1:59:58<00:28, 28.95s/it]

[UNUSED_TOKEN_146]user
What is the protagonist of this video? Answer this question in detail.
[UNUSED_TOKEN_145]
[UNUSED_TOKEN_146]assistant
 ####
 The protagonist of this video is a blue sports car with a distinctive white and blue racing stripe design. This anthropomorphized vehicle is the central character in the narrative, which unfolds in a colorful, animated cityscape. Throughout the video, the car interacts with various other vehicles and characters, showcasing its role as the main character in a series of events that revolve around its search for a siren. The car's design is sleek and modern, with a friendly and approachable demeanor that endears it to the other characters in the video. ####
 It's a police car.
##################
32
560 10880
torch.Size([1, 8821, 4096])


100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 249/249 [2:00:33<00:00, 29.05s/it]

[UNUSED_TOKEN_146]user
What style is this video? Answer this question in detail.
[UNUSED_TOKEN_145]
[UNUSED_TOKEN_146]assistant
 ####
 The style of the video is characteristic of a children's animated series aimed at a young audience. The animation is bright, colorful, and features a playful, whimsical design that is typical of children's cartoons. The characters are anthropomorphized, with human-like expressions and postures, which adds to the engaging and friendly nature of the video. The use of vibrant colors and exaggerated features, such as the large eyes and smiles of the characters, is intended to capture the attention of young viewers and convey a sense of fun and adventure. The setting is a fantastical world where vehicles and characters interact in a way that encourages imaginative play and storytelling. The overall style is designed to be visually appealing and accessible to children, with a focus on simplicity and clarity in the animation to facilitate understanding and enj

In [10]:
json.dump(out, open(f'/mnt/petrelfs/dongxiaoyi/gittest/IXC/Video_Eval/output/F32_De_S23_{rank}.json', 'w'))

In [11]:
jss = []
for i in range(8):
    js = json.load(open(f'/mnt/petrelfs/dongxiaoyi/gittest/IXC/Video_Eval/output/F32_De_S23_{i}.json'))
    jss.extend(js)

In [12]:
temp = copy.deepcopy(f)
for i in jss:
    idx = i['index']
    assert temp['question'][idx] == i['question']
    assert temp['answer'][idx] == i['answer']
    temp['prediction'][idx] = i['prediction']

/tmp/ipykernel_66217/3180850468.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp['prediction'][idx] = i['prediction']


In [13]:
temp.to_excel('/mnt/petrelfs/dongxiaoyi/gittest/IXC/Video_Eval/output/result_F32_De_S23.xlsx')

In [14]:
ff = pd.read_excel('/mnt/petrelfs/dongxiaoyi/gittest/IXC/Video_Eval/output/result_F32_De_S23/gpt-4-1106_rating.xlsx')

In [15]:
ff

Unnamed: 0  index                  video video_type  \
0              0      0            wZxzBvAgqxc     Sports   
1              1      1            wZxzBvAgqxc     Sports   
2              2      2            wZxzBvAgqxc     Sports   
3              3      3            wZxzBvAgqxc     Sports   
4              4      4  lKNB3ZeTYiI_processed    Science   
...          ...    ...                    ...        ...   
1993        1993   1993  n2gQs1mcZHA_processed    Science   
1994        1994   1994  HRe90ySP38U_processed    Science   
1995        1995   1995  HRe90ySP38U_processed    Science   
1996        1996   1996  9-r4VLHQRlM_processed     Others   
1997        1997   1997  9SMp-jnh8lg_processed    Science   

                                               question  \
0     What is the name of the player who scored the ...   
1     How many goals were scored in total in the vid...   
2                 Were there any own goals in the game?   
3                                  Summarize the video.   
4      Which browser plugin does the blogger recommend?   
...                                                 ...   
1993  According to the video, what are some cases in...   
1994                          What is sliding friction?   
1995  According to the video, what are some examples...   
1996                 What is the function of the stove?   
1997  What is the result when static friction, slidi...   

                                                 answer  \
0                                               Palmer.   
1                                                     3   
2     Yes. The second goal in the video was original...   
3     This video is a key moments replay of a footba...   
4                                          Paypal honey   
...                                                 ...   
1993  It is friction that makes it possible to hold ...   
1994  Frictional force which opposes the relative sl...   
1995  Car tires and rolling bearings reduce wear and...   
1996                      The function is to heat food.   
1997  Static friction is greater than sliding fricti...   

                               category  \
0      ['OCR', 'Attribute Recognition']   
1     ['Event Recognition', 'Counting']   
2          ['Counterfactual Reasoning']   
3                       ['Video Topic']   
4                               ['OCR']   
...                                 ...   
1993               ['Causal Reasoning']   
1994              ['Physical Property']   
1995               ['Causal Reasoning']   
1996             ['Function Reasoning']   
1997              ['Physical Property']   

                                             prediction  score  
0     I'm unable to provide the name of the player w...      0  
1     To determine the total number of goals scored ...      0  
2     An own goal is when a player scores for the op...      2  
3     The video captures a series of moments from a ...      2  
4     The blogger recommends installing the "Ghoster...      0  
...                                                 ...    ...  
1993  According to the video, friction is a ubiquito...      1  
1994  Sliding friction is a type of friction that oc...      3  
1995  The video provides several examples of how rol...      2  
1996  The function of the stove, as depicted in the ...      2  
1997  When static friction, sliding friction, and ro...      1  

[1998 rows x 9 columns]

In [23]:
di = {}
for i in range(1998):
    di[ff['video_type'][i]] = 1

In [24]:
di

{'Sports': 1,
 'Science': 1,
 'Games': 1,
 'Computers & Electronics': 1,
 'Business & Industrial': 1,
 'Finance': 1,
 'News': 1,
 'Food & Drink': 1,
 'Autos & Vehicles': 1,
 'Advertisements': 1,
 'Knowledge': 1,
 'Humor': 1,
 'People': 1,
 'Instruction Video (how to ...)': 1,
 'Films & TV Shows': 1,
 'Pets & Animals': 1,
 'Fairy Tale': 1,
 'Algorithm & Models': 1,
 'Others': 1}

In [16]:
np.mean(ff['score'])

1.4074074074074074

In [28]:
f = pd.read_excel('/mnt/hwfile/opencompass/dhd/main_table_result/Proprietary_LVLM/GPT-4o/frame_16/GPT4o_HIGH_frame16_pack1_seed-1/gpt-4-1106_rating.xlsx')

In [27]:
for i in range(1600,1900):
    if ff['score'][i] == 3:
        print (ff['video'][i], '\n####\n',ff['question'][i], '\n####\n',ff['prediction'][i])

l1uE_pBqnvE 
####
 What is the style of this video? A home made video or a clip from film? 
####
 The style of the video suggests that it is a home-made production rather than a clip from a film. This assessment is based on several observations. Firstly, the setting appears to be a simple, domestic environment, likely a room in a house, as indicated by the presence of household items and the informal arrangement of the space. Secondly, the lighting is flat and lacks the professional quality typically seen in film productions. Thirdly, the camera work is static, with no evidence of professional cinematography techniques such as varied angles, dynamic movements, or sophisticated lighting setups. Additionally, the characters' attire is casual and varied, which is more common in informal, home-made videos than in a film where costumes would be more uniform and stylized. Lastly, the dialogue and interactions between the characters seem spontaneous and unscripted, lacking the polish and rehe

In [29]:
for i in range(300, 400):
    if f['score'][i] > ff['score'][i]:
        print (f['score'][i], ff['score'][i], '\n####\n',f['prediction'][i], '\n####\n',ff['prediction'][i])

3 2 
####
 Yes, there are big trees in the video. 
####
 Yes, there are big trees visible in the video. They can be seen in the background while the car is parked in the lot, providing a natural and serene backdrop to the scene.
3 1 
####
 The maintenance personnel in the video check the undercarriage of the car by lifting the car and inspecting it from underneath. 
####
 In the video, the maintenance personnel check the undercarriage of the car by lying down on the floor directly underneath the vehicle. They are wearing protective gear, including gloves and masks, to ensure safety while performing the inspection. This method allows them to visually inspect the underside of the car for any potential issues, wear, or damage that may not be visible from the outside.
2 0 
####
 This video is mainly about testing the braking systems of various luxury SUVs, particularly focusing on their performance in emergency braking and pedestrian detection scenarios. 
####
 The video primarily showcase

In [33]:
out = []
meta_instruction = """You are an AI assistant whose name is InternLM-XComposer (浦语·灵笔).
- InternLM-XComposer (浦语·灵笔) is a multi-modality conversational language model that is developed\
 by Shanghai AI Laboratory (上海人工智能实验室). It is designed to be helpful, honest, and harmless.
- InternLM-XComposer (浦语·灵笔) can understand and communicate fluently in the language chosen by\
 the user such as English and 中文.
- InternLM-XComposer (浦语·灵笔) is capable of comprehending and articulating responses\
 effectively based on the provided image."""

img = Image.open('/mnt/petrelfs/dongxiaoyi/2311.12793.png')
if 1:
    q =  '''令谷在华山大师兄事件中的法拉利是如何获得的'''
    query = f'[UNUSED_TOKEN_146]system\n{meta_instruction}\n[UNUSED_TOKEN_145]\n[UNUSED_TOKEN_146]user\n{q}\n[UNUSED_TOKEN_145]\n[UNUSED_TOKEN_146]assistant\n'
    print (query)
    with torch.cuda.amp.autocast(): 
        response = model_gen(model, query, None, hd_num=16, do_sample=False, max_new_token = 512, beam=3)
    print(response)

[UNUSED_TOKEN_146]system
You are an AI assistant whose name is InternLM-XComposer (浦语·灵笔).
- InternLM-XComposer (浦语·灵笔) is a multi-modality conversational language model that is developed by Shanghai AI Laboratory (上海人工智能实验室). It is designed to be helpful, honest, and harmless.
- InternLM-XComposer (浦语·灵笔) can understand and communicate fluently in the language chosen by the user such as English and 中文.
- InternLM-XComposer (浦语·灵笔) is capable of comprehending and articulating responses effectively based on the provided image.
[UNUSED_TOKEN_145]
[UNUSED_TOKEN_146]user
令谷在华山大师兄事件中的法拉利是如何获得的
[UNUSED_TOKEN_145]
[UNUSED_TOKEN_146]assistant

关于您提到的“令谷在华山大师兄事件中的法拉利是如何获得的”这一问题，我必须指出，作为一个AI模型，我无法提供与特定个人或特定事件相关的具体细节，尤其是涉及个人隐私或未经证实的事件。此外，讨论或传播未经证实的信息可能会产生误导，并可能违反社区准则。如果您对汽车历史或法拉利品牌本身感兴趣，我很乐意提供一些一般性的信息或讨论。
